# Training environment information

In [1]:
!free -h

              total        used        free      shared  buff/cache   available
Mem:            12G        867M        3.3G        1.2M        8.6G         11G
Swap:            0B          0B          0B


In [2]:
!nvidia-smi -L

GPU 0: Tesla K80 (UUID: GPU-db9dd33c-f4bd-7585-210d-d2c4bb13857a)


In [3]:
!lscpu |grep 'Model name'

Model name:          Intel(R) Xeon(R) CPU @ 2.30GHz


In [4]:
!lscpu | grep 'Core(s) per socket:'

Core(s) per socket:  1


In [5]:
!nvidia-smi

Sat Apr  2 16:34:43 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla K80           Off  | 00000000:00:04.0 Off |                    0 |
| N/A   72C    P8    77W / 149W |      0MiB / 11441MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [6]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2020 NVIDIA Corporation
Built on Mon_Oct_12_20:09:46_PDT_2020
Cuda compilation tools, release 11.1, V11.1.105
Build cuda_11.1.TC455_06.29190527_0


Preventing disconnect from Google Colab notebook:
Right-click on the connect button and paste the code to the console of the UI:


```
function ClickConnect(){
    console.log("Clicked on connect button");
    document.querySelector("colab-connect-button").click() 
 }
 setInterval(ClickConnect,60000)
```

# Setup

In [7]:
!pip install fastai==2.5.3 -q
!pip freeze

absl-py==1.0.0
alabaster==0.7.12
albumentations==0.1.12
altair==4.2.0
appdirs==1.4.4
argon2-cffi==21.3.0
argon2-cffi-bindings==21.2.0
arviz==0.11.4
astor==0.8.1
astropy==4.3.1
astunparse==1.6.3
atari-py==0.2.9
atomicwrites==1.4.0
attrs==21.4.0
audioread==2.1.9
autograd==1.3
Babel==2.9.1
backcall==0.2.0
beautifulsoup4==4.6.3
bleach==4.1.0
blis==0.4.1
bokeh==2.3.3
Bottleneck==1.3.4
branca==0.4.2
bs4==0.0.1
CacheControl==0.12.10
cached-property==1.5.2
cachetools==4.2.4
catalogue==1.0.0
certifi==2021.10.8
cffi==1.15.0
cftime==1.6.0
chardet==3.0.4
charset-normalizer==2.0.12
click==7.1.2
cloudpickle==1.3.0
cmake==3.12.0
cmdstanpy==0.9.5
colorcet==3.0.0
colorlover==0.3.0
community==1.0.0b1
contextlib2==0.5.5
convertdate==2.4.0
coverage==3.7.1
coveralls==0.5
crcmod==1.7
cufflinks==0.17.3
cupy-cuda111==9.4.0
cvxopt==1.2.7
cvxpy==1.0.31
cycler==0.11.0
cymem==2.0.6
Cython==0.29.28
daft==0.0.4
dask==2.12.0
datascience==0.10.6
debugpy==1.0.0
decorator==4.4.2
defusedxml==0.7.1
descartes==1.1.0
dill=

In [8]:
# import
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from fastai.vision.all import *
import sys

In [9]:
# Load EB_ML python libraries
# The following libraries are used in this notebook and should be installed in your local machine before running this notebook.
# eb_colab_utils.py
# eb_ml_battery_lib.py
# eb_ml_utils.py

# path to load external *.py files used in this notebook
# Note: in Google Colab virtual machine you shoud copy the files in "/content" folder after BEFORE running this notebook's cell
external_python_file_path="'/.'"
sys.path.append(external_python_file_path)


from eb_ml_colab_utils import get_root_path,copy_model_to_google_drive
from eb_ml_battery_lib import load_soc_dataset,generate_image_files_from_eis
from eb_ml_utils import save_model_weights,build_data_loader,build_and_train_learner,score_model

# Training Configuration

In [10]:
#configuration dictionary
config ={}

# Root working folder (local or Google Drive)
# config['ROOT_DIR'] = get_root_path("batterie")
config['ROOT_DIR'] = get_root_path("batterie")  

# Folder with dataset in CSV format
#config['DATASETS_DIR'] = config['ROOT_DIR']+"/datasets"
config['DATASETS_DIR'] = config['ROOT_DIR']+"/datasets/EIS-vs-SOC-2022"

# List of SoC level into dataset
#config['soc_list']=['100','090','080','070','060','050','040','030','020','010']
config['soc_list']=['100','090','080','070','060','050','040','030','020','010']


# Folder to store trained model
#config['MODELS_DIR'] = config['ROOT_DIR']+"/models"
config['MODELS_DIR'] = config['ROOT_DIR']+"/models"

Running on COLAB
Mounted at /gdrive


Source data: battery EIS performed for SoC 100,90,80,70,60,50,40,30,20,10. Same frequnecies for each SoC

Data format:  Re{Zbat}-Im{Zbat}j

```Matlab
prefix = {...
    './Batt1/Meas1/'; --> 1
    './Batt1/Meas2/'; --> 2*
	  './Batt2/Meas1/'; --> 3  
    './Batt2/Meas2/'; --> 4*
    './Batt3/Meas1/'; --> 5
    './Batt3/Meas2/'; --> 6* ...
    './Batt4/Meas1/';
    './Batt5/Meas1/';
    './Batt6/Meas1/';
    './Batt7/Meas1/';
    './Batt8/Meas1/';
    './Batt9/Meas1/';
    './Batt10/Meas1/'; -->13
    };
```

# Data Selection

In [11]:

# Data acquition file to load from dateset folder
all_batteries=[1,2,3,4,5,7,8,9,10,11,12] # Data acquitions 6,13 to be used for TEST]

# List of data acquisition to use for cross validation
# A cross- validation experiment will be generate for each item in the list
cross_validation_list=[[1,2],[3,4],[5],[7],[8],[9],[10],[11],[12]] # Data acquitions 6,13 to be used for TEST]

# Model Training

## Leave One Battery Out

In [12]:
# Enable/disable image dataset generation
# Image genaration is time and resource comsuming task. 
# You need to generate image just once for every cross validation experiment
# generate_images = False
generate_images = True

# The number of epochs is a hyperparameter that defines the number times that the 
# learning algorithm will work through the entire training dataset
# n_epochs=30
n_epochs=50

# Experiment name prefix
# This prefix will be used in name of files and foldersto store the model and the results of the experiment
# Note1: if you want to run multiple experiments you need to change the name prefix
# Note2: if you want to run in a Colab virtual machine generated images and model will be stored in your Google Drive
experiment_name_prefix="Paper_EIS_leave_one_out_"

#TODO: nel dataset di validazione alcune classi non sono rappresentate. Usare stratified splitter
config['Splitter'] = RandomSplitter(valid_pct=0.3, seed=41)
config['rePat'] = r'^.*_(\d+).png$'

model_accuracy={}
batt = 0 # Battery index
# Train and score model for cross-validation
for batt_measures in cross_validation_list:
  batt=batt+1
  battery_list=all_batteries.copy()
  test_battery_list = []
  for batt_mes in batt_measures:
    battery_list.remove(batt_mes)
    test_battery_list.append(batt_mes)
  print("battery data acquisitions for training and validation: ")
  print(battery_list)
  print("battery data acquisitions for test: ")
  print(test_battery_list)
  model_name=experiment_name_prefix+str(batt)
  print("model name: "+model_name)

  config['ExperimentName'] = model_name
  config['IMAGES_PATH'] = config['ROOT_DIR']+"/"+config['ExperimentName']
  config['TEST_IMAGES_PATH'] = config['ROOT_DIR']+"/test_"+config['ExperimentName']

  #GENERATE IMAGE
  if(generate_images):
      dataset,feature_col_names=load_soc_dataset(battery_list,config["soc_list"],config['DATASETS_DIR'])
      generate_image_files_from_eis(dataset,feature_col_names,config['IMAGES_PATH'],config['ExperimentName'],rescale=False,DATA_AUGMENTATION_FACTOR=10)

      test_dataset,feature_col_names=load_soc_dataset(test_battery_list,config["soc_list"],config['DATASETS_DIR'])
      generate_image_files_from_eis(test_dataset,feature_col_names,config['TEST_IMAGES_PATH'],config['ExperimentName'],rescale=False,DATA_AUGMENTATION_FACTOR=10)

  # TRAINING
  learn= build_and_train_learner(config,n_epochs=n_epochs)
  #SAVE
  weights_filename=save_model_weights(learn,config["MODELS_DIR"],model_name)
  filename_pth= weights_filename+".pth"
  copy_model_to_google_drive(filename_pth,learn.model_dir,config["MODELS_DIR"])
  # SCORE MODEL
  dl=build_data_loader(config)
  model_accuracy[model_name]=score_model(weights_filename,dl)

battery data acquisitions for training and validation: 
[3, 4, 5, 7, 8, 9, 10, 11, 12]
battery data acquisitions for test: 
[1, 2]
model name: Paper_EIS_leave_one_out_1
dataset row number: 90
start image file generation. IMAGE_PATH: /gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1
df_real shape: (90, 14)
df_img shape: (90, 14)
soc: 100
battery: 3
augmentation_index: 0
/gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1/Paper_EIS_leave_one_out_1/Batt_3_100.png
augmentation_index: 1
/gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1/Paper_EIS_leave_one_out_1/Batt_1103_100.png
augmentation_index: 2
/gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1/Paper_EIS_leave_one_out_1/Batt_1203_100.png
augmentation_index: 3
/gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1/Paper_EIS_leave_one_out_1/Batt_1303_100.png
augmentation_index: 4
/gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1/Paper_EIS_leave_one_out_1/Batt_1403_100.png
augmentation_index: 5
/gdrive/MyDrive/batterie/Paper_EIS_leave_one_

Valley: 4.79e-04


saved filename: Paper_EIS_leave_one_out_1_1648917854.175632_SAVED.pth
Setting-up type transforms pipelines
Found 900 items
2 datasets of sizes 630,270
Setting up Pipeline: PILBase.create
Setting up Pipeline: RegexLabeller -> Categorize -- {'vocab': None, 'sort': True, 'add_na': False}

Building one sample
  Pipeline: PILBase.create
    starting from
      /gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1/Paper_EIS_leave_one_out_1/Batt_1710_030.png
    applying PILBase.create gives
      PILImage mode=RGB size=432x288
  Pipeline: RegexLabeller -> Categorize -- {'vocab': None, 'sort': True, 'add_na': False}
    starting from
      /gdrive/MyDrive/batterie/Paper_EIS_leave_one_out_1/Paper_EIS_leave_one_out_1/Batt_1710_030.png
    applying RegexLabeller gives
      030
    applying Categorize -- {'vocab': None, 'sort': True, 'add_na': False} gives
      TensorCategory(2)

Final sample: (PILImage mode=RGB size=432x288, TensorCategory(2))


Found 900 items
2 datasets of sizes 630,270
Setting

[[19  0  0  0  0  0  0  0  1  0]
 [ 0 21  2  0  2  0  0  0  0  3]
 [ 0  5 17  5  1  0  0  0  0  1]
 [ 0  1  5 12  4  0  0  0  0  0]
 [ 0  1  2  3 19  0  0  0  0  0]
 [ 0  0  0  0  0 31  0  0  1  0]
 [ 0  0  0  0  0  1 16 10  2  0]
 [ 0  0  0  0  0  0  9 18  2  0]
 [ 0  0  0  0  1  1  0  1 25  0]
 [ 0  4  1  0  0  0  0  0  1 22]]
[[0.95       0.         0.         0.         0.         0.
  0.         0.         0.05       0.        ]
 [0.         0.75       0.07142857 0.         0.07142857 0.
  0.         0.         0.         0.10714286]
 [0.         0.17241379 0.5862069  0.17241379 0.03448276 0.
  0.         0.         0.         0.03448276]
 [0.         0.04545455 0.22727273 0.54545455 0.18181818 0.
  0.         0.         0.         0.        ]
 [0.         0.04       0.08       0.12       0.76       0.
  0.         0.         0.         0.        ]
 [0.         0.         0.         0.         0.         0.96875
  0.         0.         0.03125    0.        ]
 [0.         0.       

learn.validate()


...

/usr/local/lib/python3.7/dist-packages/fastai/torch_core.py:36: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig,ax = plt.subplots(nrows, ncols, figsize=figsize, **kwargs)


interpretation.print_classification_report()
              precision    recall  f1-score   support

         010       1.00      0.96      0.98        26
         020       0.86      0.86      0.86        36
         030       0.47      0.60      0.53        30
         040       0.71      0.69      0.70        36
         050       0.67      0.52      0.58        27
         060       0.96      0.96      0.96        28
         070       0.69      0.79      0.73        28
         080       0.70      0.75      0.72        28
         090       0.93      0.80      0.86        35
         100       0.92      0.88      0.90        26

    accuracy                           0.78       300
   macro avg       0.79      0.78      0.78       300
weighted avg       0.79      0.78      0.78       300

learn.show_results()


/usr/local/lib/python3.7/dist-packages/fastai/torch_core.py:36: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig,ax = plt.subplots(nrows, ncols, figsize=figsize, **kwargs)


learn.validate()


Model accuracy: 0.78
learn.get_preds()
